In [3]:
%cd D:\updated\Chatty-V2

D:\updated\Chatty-V2


In [27]:
import pickle as pkl
raw = pkl.load(open( "webscrap1.pkl", "rb" ))
raw

[array([' Original Airdate', ', 1963       GIRL:  Night, Miss Wright.',
        '  BARBARA:  Wait in here, please, Susan. I wont be long.',
        '  BOY:  Goodnight, Miss Wright.', '    IAN:  Oh? Not gone yet?',
        '  BARBARA:  Obviously not.',
        '  IAN:  Right, ask a silly question.', '  BARBARA:  Im sorry.',
        '  IAN:  Thats all right. Ill forgive you this time.',
        '  BARBARA:  Oh, I had a terrible day. I dont know what to make of it.',
        '  IAN:  Oh, whats the trouble? Can I help?',
        '  BARBARA:  Oh, its one of the girls, Susan Foreman.',
        '  IAN:  Susan Foreman? She your problem too?', '  BARBARA:  Yes.',
        '  IAN:  You dont know what to make of her?', '  BARBARA:  No.',
        '  IAN:  How old is she, Barbara?', '  BARBARA:  Fifteen.',
        '  IAN:  Fifteen. She lets her knowledge out a bit at a time so as not to embarrass me. Thats what I feel about her. She knows more science than Ill ever know. Shes a genius. Is that what 

Remove spaces before each line, split each row into two columns: speaker and text. Remove all punctuation

In [ ]:
import pandas as pd
import string
from tqdm import tqdm #side note i really love tqdm
df = pd.DataFrame(columns=['Raw','Person', 'Text', 'Ep'])
i = 1
ignored = 0
for ep in tqdm(raw):
    for line in ep:
        line = line.lower()
        splitty = line.split(":")
        if len(splitty) > 1:
            df = df.append({'Raw':line, 'Ep':i}, ignore_index=True)
        else:
            ignored += 1
    i+=1 

 84%|█████████████████████████████████████████████████████████████████▋            | 218/259 [2:18:41<21:00, 30.74s/it]

The last cell took around 2 hours, in the future, append those fields in a list and then append that whole thing into the dataframe later

In [ ]:
# df.to_csv("all_ep_raw.csv")
df.head()

In [ ]:
def give_person(line):
    return line.Raw.split(":")[0].strip()
def give_line(line):
    text = line.Raw.split(":")[1]
    return text.translate(str.maketrans('', '', string.punctuation)).strip()
df["Person"] = df.apply(give_person) 
df["Text"] = df.apply(give_line) 
df.head()

In [ ]:
print(len(df)) # please be more than 300

In [ ]:
df.loc[df['Person'] != 'DOCTOR', 'Person'] = 'COMPANION'
df["counts"] = df["Text"].str.split().str.len()
df = df.reset_index(drop=True)
print("Sentences in total: {}".format(len(raw)))
print("DOCTOR")
print("Max words per sentence: {}, Avg words per sentence: {}".format(max(df[df.Person=='DOCTOR'].counts),df[df.Person=='DOCTOR'].counts.mean()))
print("COMPANION")
print("Max words per sentence: {}, Avg words per sentence: {}".format(max(df[df.Person=='COMPANION'].counts),df[df.Person=='COMPANION'].counts.mean()))
df["Person"].value_counts()[:10].plot.bar()

In [ ]:
eps = df.Ep.unique()
print("# of Episodes: {}".format(len(eps)))

We need to make it so that it's only the doctor talking to the companion, no companion to companion.
Note that companion is x, doctor is y
We first split by episode, then we check whether doctor talks under a companion, if not, line is removed

In [ ]:
sep_eps = []
remove_these = []
X = []
Y = []
def sift(line):
    index = line.name
    if (line["Person"] == "COMPANION" and line["shift_Person"] == "DOCTOR"):
        X.append(line["Text"])
        Y.append(line["shift_Text"])
    else:
        remove_these.append(index)
for i in tqdm(range(len(eps))):
    ep_df = df[df["Ep"]==eps[i]]
    ep_df["shift_Person"] = df['Person'].shift(-1)
    ep_df["shift_Text"] = df['Text'].shift(-1)
    ep_df.apply(sift)
    ep_df = ep_df.drop(remove_these)
    remove_these = []
    sep_eps.append(ep_df)

In [ ]:
X_ = pd.DataFrame(X)
Y_ = pd.DataFrame(Y)
X_.to_csv("X_1.csv")
Y_.to_csv("Y_1.csv")